# Purpose
The goal of this is to show how we can create a dataset from a recent open-source example. I came across **Science QA** and thought it would be a great example as its quite interesting and it is multi-modal.

# Get the data
## 1. Where is the data?
A quick google search shows that this data has a [repo](https://github.com/lupantech/ScienceQA#download-the-dataset). 

> The text part of the ScienceQA dataset is provided in data/scienceqa/problems.json. You can download the image data of ScienceQA by running:
>
>    . tools/download.sh

We can see in the quoted section that the data text is in a json, and the images can be accessed through the shell script. I modified the script to match this repo's structure and put it here: [download.sh](./download.sh). 

Lets run the script and download the json so we have the data locally in our folder structure.

Download images to the `images` folder:

In [1]:
!./download.sh

Download the json file to the `text` folder:

In [2]:
!wget -nc https://raw.githubusercontent.com/lupantech/ScienceQA/main/data/scienceqa/problems.json -P ./text

File ‘./text/problems.json’ already there; not retrieving.



In [3]:
%pip install datasets==2.9.0

Note: you may need to restart the kernel to use updated packages.


In [4]:
from datasets import load_dataset

In [5]:
load_dataset("json", data_files="text/problems.json")

Using custom data configuration default-f6bbdcd7a9e39254


Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Failed to read file '/Users/derekthomas/projects/datasets/scienceQA/text/problems.json' with error <class 'pyarrow.lib.ArrowInvalid'>: JSON parse error: Column() changed from object to string in row 0


DatasetGenerationError: An error occurred while generating the dataset

Oh no! What happened?

> Not able to read records in the JSON file at ... You should probably indicate the field of the JSON file containing your records. This JSON file contain the following fields [1 ... 21208] Select the correct one and provide it as `field='XXX'` to the dataset loading method. 

But what does that even mean? First lets examine our record:

``` json
{
  "1":{
    "question":"Which of these states is farthest north?",
    "choices":[
      "West Virginia",
      "Louisiana",
      "Arizona",
      "Oklahoma"
    ],
    "answer":0,
    "hint":"",
    "image":"image.png",
    "task":"closed choice",
    "grade":"grade2",
    "subject":"social science",
    "topic":"geography",
    "category":"Geography",
    "skill":"Read a map: cardinal directions",
    "lecture":"Maps have four cardinal directions, or main directions. Those directions are north, south, east, and west.\nA compass rose is a set of arrows that point to the cardinal directions. A compass rose usually shows only the first letter of each cardinal direction.\nThe north arrow points to the North Pole. On most maps, north is at the top of the map.",
    "solution":"To find the answer, look at the compass rose. Look at which way the north arrow is pointing. West Virginia is farthest north.",
    "split":"train"
  }
}
```

We can see that the image folder name is not contained in the record, but overall we have 1 record per image.

There are 2 main ways we load jsons [list of records, or by field] are not going to work. We are going to have to write a custom loader, but we are quite close.

In [6]:
import datasets

In [7]:
class ScienceQA(datasets.GeneratorBasedBuilder):
    """Science Question Answering (ScienceQA), a new benchmark that consists of 21,208 multimodal 
    multiple choice questions with a diverse set of science topics and annotations of their answers 
    with corresponding lectures and explanations. 
    The lecture and explanation provide general external knowledge and specific reasons,
    respectively, for arriving at the correct answer."""

    VERSION = datasets.Version("1.0.0")

#     def _info(self):
#         # TODO: This method specifies the datasets.DatasetInfo object which contains informations and typings for the dataset
#         features = datasets.Features(
#             {
#                 "image_id": datasets.Value("string"),
#                 "choices": datasets.features.Sequence()
#                 "option1": datasets.Value("string"),
#                 "answer": datasets.Value("string")
#                 # These are the features of your dataset like images, labels ...
#             }
#         )
#         return datasets.DatasetInfo(
#             # This is the description that will appear on the datasets page.
#             description=_DESCRIPTION,
#             # This defines the different columns of the dataset and their types
#             features=features,  # Here we define them above because they are different between the two configurations
#             # If there's a common (input, target) tuple from the features, uncomment supervised_keys line below and
#             # specify them. They'll be used if as_supervised=True in builder.as_dataset.
#             # supervised_keys=("sentence", "label"),
#             # Homepage of the dataset for documentation
#             homepage=_HOMEPAGE,
#             # License for the dataset if available
#             license=_LICENSE,
#             # Citation for the dataset
#             citation=_CITATION,
#         )

#     def _split_generators(self, dl_manager):
#         # TODO: This method is tasked with downloading/extracting the data and defining the splits depending on the configuration
#         # If several configurations are possible (listed in BUILDER_CONFIGS), the configuration selected by the user is in self.config.name

#         # dl_manager is a datasets.download.DownloadManager that can be used to download and extract URLS
#         # It can accept any type or nested list/dict and will give back the same structure with the url replaced with path to local files.
#         # By default the archives will be extracted and a path to a cached folder where they are extracted is returned instead of the archive
#         urls = _URLS[self.config.name]
#         data_dir = dl_manager.download_and_extract(urls)
#         return [
#             datasets.SplitGenerator(
#                 name=datasets.Split.TRAIN,
#                 # These kwargs will be passed to _generate_examples
#                 gen_kwargs={
#                     "filepath": os.path.join(data_dir, "train.jsonl"),
#                     "split": "train",
#                 },
#             ),
#             datasets.SplitGenerator(
#                 name=datasets.Split.VALIDATION,
#                 # These kwargs will be passed to _generate_examples
#                 gen_kwargs={
#                     "filepath": os.path.join(data_dir, "dev.jsonl"),
#                     "split": "dev",
#                 },
#             ),
#             datasets.SplitGenerator(
#                 name=datasets.Split.TEST,
#                 # These kwargs will be passed to _generate_examples
#                 gen_kwargs={
#                     "filepath": os.path.join(data_dir, "test.jsonl"),
#                     "split": "test"
#                 },
#             ),
#         ]

    # method parameters are unpacked from `gen_kwargs` as given in `_split_generators`
    def _generate_examples(self, filepath, split):
        # TODO: This method handles input defined in _split_generators to yield (key, example) tuples from the dataset.
        # The `key` is for legacy reasons (tfds) and is not important in itself, but must be unique for each example.
        with open(filepath, encoding="utf-8") as f:
            for key, row in enumerate(f):
                data = json.loads(row)
                if self.config.name == "first_domain":
                    # Yields examples as (key, example) tuples
                    yield key, {
                        "sentence": data["sentence"],
                        "option1": data["option1"],
                        "answer": "" if split == "test" else data["answer"],
                    }
                else:
                    yield key, {
                        "sentence": data["sentence"],
                        "option2": data["option2"],
                        "second_domain_answer": "" if split == "test" else data["second_domain_answer"],
                    }

In [8]:
import json

In [9]:
with open('text/problems.json', encoding="utf-8") as f:
    data = json.load(f)
    for image_id, row in data.keys():
        print(data)
        break

In [10]:
data.keys()

dict_keys(['1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '20', '21', '22', '23', '24', '25', '26', '27', '28', '29', '30', '31', '32', '33', '34', '35', '36', '37', '38', '39', '40', '41', '42', '43', '44', '45', '46', '47', '48', '49', '50', '51', '52', '53', '54', '55', '56', '57', '58', '59', '60', '61', '62', '63', '64', '65', '66', '67', '68', '69', '70', '71', '72', '73', '74', '75', '76', '77', '78', '79', '80', '81', '82', '83', '84', '85', '86', '87', '88', '89', '90', '91', '92', '93', '94', '95', '96', '97', '98', '99', '100', '101', '102', '103', '104', '105', '106', '107', '108', '109', '110', '111', '112', '113', '114', '115', '116', '117', '118', '119', '120', '121', '122', '123', '124', '125', '126', '127', '128', '129', '130', '131', '132', '133', '134', '135', '136', '137', '138', '139', '140', '141', '142', '143', '144', '145', '146', '147', '148', '149', '150', '151', '152', '153', '154', '155', '156', '157'